# Note, a geojson is needed for Folium. Json can be found ===> [here:](https://github.com/python-visualization/folium/blob/master/examples/data/world-countries.json) <====

In [393]:
# Needed import
import folium
from folium import plugins
import json
import pandas as pd
import geopandas
import math
import numpy as np
import base64
import matplotlib.pyplot as plt
from folium import IFrame
import branca

In [2]:
# Any df with those following columns should be fine, as an example, you can take those
df_final = pd.read_pickle("./data/final_df.pkl")
df_final['profit'] = df_final['export_v'] - df_final['import_v']
df_final['diff_quantity'] = df_final['export_q'] - df_final['import_q']
df_final['import_vpq'] = df_final['import_v'] / df_final['import_q']
df_final['export_vpq'] = df_final['export_v'] / df_final['export_q']
df_final[(df_final['item_trades']=='Wheat')&(df_final['year']==2016)]

area_code                               area_crops item_crops  year  \
67              1                                  Armenia      Wheat  2016   
1678            2                              Afghanistan      Wheat  2016   
3987            3                                  Albania      Wheat  2016   
7031            4                                  Algeria      Wheat  2016   
12789           7                                   Angola      Wheat  2016   
...           ...                                      ...        ...   ...   
957759       5801                Least Developed Countries      Wheat  2016   
968593       5802         Land Locked Developing Countries      Wheat  2016   
979113       5803           Small Island Developing States      Wheat  2016   
987670       5815        Low Income Food Deficit Countries      Wheat  2016   
999207       5817  Net Food Importing Developing Countries      Wheat  2016   

       item_trades  area_harvested   production    yield   export_q  export_v  \
67           Wheat        108049.0     350369.0  32427.0       16.0       6.0   
1678         Wheat       2300210.0    4555110.0  19803.0        0.0       0.0   
3987         Wheat         70512.0     275000.0  39000.0      741.0     195.0   
7031         Wheat       2062179.0    2440097.0  11833.0        NaN       NaN   
12789        Wheat          4295.0       3333.0   7760.0        NaN       NaN   
...            ...             ...          ...      ...        ...       ...   
957759       Wheat       5797356.0   13312832.0  22964.0     5433.0    2169.0   
968593       Wheat      23428059.0   41924247.0  17895.0  6007991.0  950364.0   
979113       Wheat             5.0          9.0  17206.0     2011.0     675.0   
987670       Wheat      48806439.0  142243503.0  29144.0   269639.0   68788.0   
999207       Wheat      20016478.0   52865900.0  26411.0    51673.0   11658.0   

        ...  hs12_code  parent_group child_group parent_description  \
67      ...     100111            10        1001            Cereals   
1678    ...     100111            10        1001            Cereals   
3987    ...     100111            10        1001            Cereals   
7031    ...     100111            10        1001            Cereals   
12789   ...     100111            10        1001            Cereals   
...     ...        ...           ...         ...                ...   
957759  ...     100111            10        1001            Cereals   
968593  ...     100111            10        1001            Cereals   
979113  ...     100111            10        1001            Cereals   
987670  ...     100111            10        1001            Cereals   
999207  ...     100111            10        1001            Cereals   

       child_description ISO3 Code      profit diff_quantity  import_vpq  \
67      Wheat and meslin       ARM    -60114.0     -288803.0    0.208158   
1678    Wheat and meslin       AFG    -44738.0     -258473.0    0.173086   
3987    Wheat and meslin       ALB    -42843.0     -206267.0    0.207905   
7031    Wheat and meslin       DZA         NaN           NaN    0.217669   
12789   Wheat and meslin       AGO         NaN           NaN    0.309091   
...                  ...       ...         ...           ...         ...   
957759  Wheat and meslin       NaN  -4102419.0   -18296643.0    0.224269   
968593  Wheat and meslin       NaN  -1257016.0    -3954443.0    0.221570   
979113  Wheat and meslin       NaN   -748579.0    -2791715.0    0.268192   
987670  Wheat and meslin       NaN  -6783606.0   -31204885.0    0.217712   
999207  Wheat and meslin       NaN -10513459.0   -48378515.0    0.217326   

        export_vpq  
67        0.375000  
1678           NaN  
3987      0.263158  
7031           NaN  
12789          NaN  
...            ...  
957759    0.399227  
968593    0.158183  
979113    0.335654  
987670    0.255111  
999207    0.225611  

[156 rows x 22 columns]

### Below is the main function.
Example of how to use it follows in the next cell.

In [783]:
def to_hex_c(color):
    res = hex(int(color * 255))[2:]
    return '0' + res if len(res) == 1 else res

def show_production_all_countries(df, year, products=None, coloring='profit', filename='folium/countries_profit.html', cmap='inferno', diverging=False, normalized=True):
    """
    Complete function that takes some predefined df and output a map of the requested food for a given year.
    Show a folium map and then save the plot in an html file
    """
    
    
    df = df[df['year'] == year]
    df = df.replace([np.inf, -np.inf], np.nan)
    world = geopandas.read_file(geopandas.datasets.get_path('naturalearth_lowres'))
    
    # Debugging known anomalies
    world.at[21, 'iso_a3'] = 'NOR'
    world.at[43, 'iso_a3'] = 'FRA'
    world.at[160, 'iso_a3'] = 'CYP'
    world.at[167, 'iso_a3'] = 'SOM'
    world.at[174, 'iso_a3'] = 'RKS'
    
    df = df.merge(world[['pop_est', 'iso_a3']], left_on='ISO3 Code', right_on='iso_a3', how='outer')
    global_min = 0
    global_max = 1
    highest_population = world['pop_est'].max()
    if normalized:
        
        df['profit_norm'] = df['profit'] / df['pop_est']
        df['export_v_norm'] = df['export_v'] / df['pop_est']
        df['import_v_norm'] = df['import_v'] / df['pop_est']
        df['diff_quantity_norm'] = df['diff_quantity'] / df['pop_est']
        df['export_q_norm'] = df['export_q'] / df['pop_est']
        df['import_q_norm'] = df['import_q'] / df['pop_est']
    
    isFirst = True
        
    if products == None:
        products = df.item_trades[:10]
    
    
    #layer_types = ['value', 'quantity']
    m = folium.Map([40,0], zoom_start=2, min_zoom=2)
    #fg = folium.FeatureGroup(overlay=True, name='groups', control=False)
    #m.add_child(fg)
    
    by_product = df.groupby('item_trades')
    i = 0
    for product in products:
        df_product = by_product.get_group(product)
        
        global_min = min(global_min, df_product[coloring].min())
        global_max = max(global_max, df_product[coloring].max())

        countries = geopandas.read_file('data/world-countries.json')
        #cm = countries.merge(df, left_on='id', right_on='iso3_code')
        cm = countries.merge(df_product, left_on='id', right_on='ISO3 Code')
        
             
        
        cm['profit'] = cm['profit'].apply(lambda value : 0 if math.isnan(value) else f'{int(value):,}')
        cm['export_v'] = cm['export_v'].apply(lambda value : 0 if math.isnan(value) else f'{int(value):,}')
        cm['import_v'] = cm['import_v'].apply(lambda value : 0 if math.isnan(value) else f'{int(value):,}')
        cm['pop_est'] = cm['pop_est'].apply(lambda value : 0 if math.isnan(value) else f'{int(value):,}')

        cm['diff_quantity'] = cm['diff_quantity'].apply(lambda value : 0 if math.isnan(value) else f'{int(value):,}')
        cm['export_q'] = cm['export_q'].apply(lambda value : 0 if math.isnan(value) else f'{int(value):,}')
        cm['import_q'] = cm['import_q'].apply(lambda value : 0 if math.isnan(value) else f'{int(value):,}')

        cm['export_vpq'] = cm['export_vpq'].apply(lambda value : 0 if math.isnan(value) else f'{value:.2f}')
        cm['import_vpq'] = cm['import_vpq'].apply(lambda value : 0 if math.isnan(value) else f'{value:.2f}')
                
        if normalized:
            cm = cm[['id', 'name', 'pop_est', 'profit_norm', 'export_v_norm', 'import_v_norm', 'diff_quantity_norm', 'export_q_norm', 'import_q_norm',
                 'geometry', 'item_trades', 'export_q', 'import_q', 'export_v', 'import_v', 'ISO3 Code', 'profit', 'diff_quantity', 'import_vpq', 'export_vpq']]
        else:
            cm = cm[['id', 'name', 'pop_est',
                 'geometry', 'item_trades', 'export_q', 'import_q', 'export_v', 'import_v', 'ISO3 Code', 'profit', 'diff_quantity', 'import_vpq', 'export_vpq']]
        cm.to_file("data/countries-production.json", driver='GeoJSON')
        geo_json_data = json.load(open('data/countries-production.json'))

        def my_color_function(feature):
            """Maps high values to green and negative values to red."""
            
            color_feature = coloring
            if normalized:
                color_feature += "_norm"
            
            
            if len(df[df['ISO3 Code'] == feature['properties']['id']][color_feature]) == 0:
                return '#ffffff'
            value = df[(df['ISO3 Code'] == feature['properties']['id'])&(df['item_trades'] == feature['properties']['item_trades'])][color_feature].iloc[0]
            feat = feature['properties']['item_trades']
            min_val = (df[df['item_trades']== feat])[color_feature].min()
            max_val = (df[df['item_trades']== feat])[color_feature].max()
            min_val = 0 if math.isinf(min_val) else min_val
            max_val = 100000 if math.isinf(max_val) else max_val

            if math.isnan(value) or math.isinf(value):
                return "#BEBEBE"
            
            
            
            colormap = plt.get_cmap(cmap)
            if diverging:
                if value > 0:
                    color = colormap(0.5 + value/(2*max_val))
                else:
                    color = colormap(0.5 - value/(2*min_val))
            else:
                color = colormap( (value - min_val)/(max_val - min_val))
                
                
            return '#' + to_hex_c(color[0]) + to_hex_c(color[1]) + to_hex_c(color[2])
            
            

        def my_highlight_function(feature):
            return {
                'fillColor': 'black',
                'fillOpacity': 0.5,
                'color' : 'black',
                'weight' : 3,
                'dashArray' : '5, 5'
                }

        
        layer = folium.GeoJson(
            geo_json_data,
            style_function=lambda feature: {
                'fillColor': my_color_function(feature),
                'fillOpacity': 0.9,
                'color' : 'black',
                'weight' : 1.5,
                'dashArray' : '5, 5'
                },
            overlay=True,
            show=isFirst,
            highlight_function=my_highlight_function,
            tooltip=folium.features.GeoJsonTooltip(
                opacity=1,
                fields=['name', 'pop_est', 'profit', 'export_v', 'import_v', 'diff_quantity', 'export_q', 'import_q', 'export_vpq', 'import_vpq'],
                aliases=['State name:', 'population estimation [Hab.]:',  'Gross Profit [1,000$]:', 'Export value [1,000$]:', 'Import value [1,000$]: ', 'Difference of quantity [Tonnes]:', 'Export quantity [Tonnes]:', 'Import quantity [Tonnes]:', 'Export V/Q [1,000$/Tonnes]:', 'Import V/Q [1,000$/Tonnes]:'],
                )
            )
        #g = plugins.FeatureGroupSubGroup(fg, coloring, show=False)
        #m.add_child(g)
        isFirst = False
        
        layer.layer_name = product
        layer.add_to(m)
        
        #layer.add_to(fg)
        
    plugins.Fullscreen(
        position='bottomright',
        title='Expand me',
        title_cancel='Exit me',
        force_separate_button=True
    ).add_to(m)
    if normalized:
        global_min /= highest_population
        global_max /= highest_population
        
    colormapL = branca.colormap.linear.RdYlGn_09.scale(global_min, global_max)
    colormapL = colormapL.to_step(index=[global_min, global_min/2, 0, global_max/2, global_max])
    
    
    title = {'profit' : 'Gross Profit', 'diff_quantity' : 'Difference of Quantity', 'import_q' : 'import Quantity', 'export_q': 'Export Quantity',
            'import_v': 'Import Value', 'export_v' : 'Export Value', 'import_vpq' : 'Import Value per Quantity', 'export_vpq' : 'Export Value per Quantity'}
    colormapL.caption = title.get(coloring, coloring) + " (in " + str(year) +")" if not normalized else title.get(coloring, coloring) + " per population" + " (in " + str(year) +")"
    colormapL.add_to(m)  
    folium.LayerControl().add_to(m)
    
    m.save(filename)
    return m

In [784]:
# Example: Show a specific list of product, in year 2017. Color in function of "diff_quantity" column
#show_production_all_countries(df_final, 2016, ['Wheat', 'Flour, wheat'], coloring='diff_quantity', filename='folium/wheat_2016_diff_quantity.html', cmap='PuOr', diverging=True)

In [785]:
df_avocado = pd.read_pickle("./data/avocado_df.pkl")
df_avocado.fillna(0, inplace=True)
df_avocado['profit'] = df_avocado['export_v'] - df_avocado['import_v']
df_avocado['diff_quantity'] = df_avocado['export_q'] - df_avocado['import_q']
df_avocado['import_vpq'] = df_avocado['import_v'] / df_avocado['import_q']
df_avocado['export_vpq'] = df_avocado['export_v'] / df_avocado['export_q']
df_avocado.head(2)

area_code item_crops item_key  year  area_harvested  production  yield  \
0          9   Avocados  avocado  1961             0.0      2000.0    0.0   
1          9   Avocados  avocado  1962             0.0      3000.0    0.0   

  item_trades  export_q  export_v  ...  ISO3 Code  hs12_code parent_group  \
0    Avocados       0.0       0.0  ...        ARG     080440           08   
1    Avocados       0.0       0.0  ...        ARG     080440           08   

  child_group                                 parent_description  \
0        0804  Fruit and nuts, edible; peel of citrus fruit o...   
1        0804  Fruit and nuts, edible; peel of citrus fruit o...   

                                   child_description profit diff_quantity  \
0  Dates, figs, pineapples, avocados, guavas, man...    0.0           0.0   
1  Dates, figs, pineapples, avocados, guavas, man...    0.0           0.0   

  import_vpq  export_vpq  
0        NaN         NaN  
1        NaN         NaN  

[2 rows x 23 columns]

In [786]:
show_production_all_countries(df_avocado, 2016, ['Avocados'], coloring='profit', filename='folium/avocados_2016_profit.html', cmap='RdYlGn', diverging=True, normalized=True)

In [787]:
df_coffee = pd.read_pickle("./data/coffee_df.pkl")
df_coffee.fillna(0, inplace=True)
df_coffee['profit'] = df_coffee['export_v'] - df_coffee['import_v']
df_coffee['diff_quantity'] = df_coffee['export_q'] - df_coffee['import_q']
df_coffee['import_vpq'] = df_coffee['import_v'] / df_coffee['import_q']
df_coffee['export_vpq'] = df_coffee['export_v'] / df_coffee['export_q']
df_coffee.head(2)

area_code     item_crops item_key  year  area_harvested  production  \
0          7  Coffee, green    coffe  1961        350000.0    168600.0   
1          7  Coffee, green    coffe  1961        350000.0    168600.0   

    yield       item_trades  export_q  export_v  ...  ISO3 Code  hs12_code  \
0  4817.0  Coffee, extracts       0.0       0.0  ...        AGO     090111   
1  4817.0     Coffee, green  118210.0   48670.0  ...        AGO     090111   

  parent_group child_group            parent_description  \
0           09        0901  Coffee, tea, mate and spices   
1           09        0901  Coffee, tea, mate and spices   

                                   child_description   profit diff_quantity  \
0  Coffee, whether or not roasted or decaffeinate...      0.0           0.0   
1  Coffee, whether or not roasted or decaffeinate...  48640.0      118190.0   

  import_vpq  export_vpq  
0        NaN         NaN  
1        1.5    0.411725  

[2 rows x 23 columns]

In [788]:
products = list(df_coffee.item_trades.unique())[:-1]
show_production_all_countries(df_coffee, 2016, products, coloring='profit', filename='folium/coffee_2016_profit.html', cmap='RdYlGn', diverging=True, normalized=True)

In [789]:
df_tobacco = pd.read_pickle("./data/tobacco_df.pkl")
df_tobacco.fillna(0, inplace=True)
df_tobacco['profit'] = df_tobacco['export_v'] - df_tobacco['import_v']
df_tobacco['diff_quantity'] = df_tobacco['export_q'] - df_tobacco['import_q']
df_tobacco['import_vpq'] = df_tobacco['import_v'] / df_tobacco['import_q']
df_tobacco['export_vpq'] = df_tobacco['export_v'] / df_tobacco['export_q']
df_tobacco.head(2)

area_code               item_crops item_key  year  area_harvested  \
0          1  Tobacco, unmanufactured  tobacco  1961             0.0   
1          1  Tobacco, unmanufactured  tobacco  1961             0.0   

   production  yield           item_trades  export_q  export_v  ...  \
0         0.0    0.0            Cigarettes       0.0       0.0  ...   
1         0.0    0.0  Tobacco products nes       0.0       0.0  ...   

   ISO3 Code  hs12_code parent_group child_group  \
0        ARM     240110           24        2401   
1        ARM     240110           24        2401   

                             parent_description  \
0  Tobacco and manufactured tobacco substitutes   
1  Tobacco and manufactured tobacco substitutes   

                         child_description profit diff_quantity import_vpq  \
0  Tobacco, unmanufactured; tobacco refuse    0.0           0.0        NaN   
1  Tobacco, unmanufactured; tobacco refuse    0.0           0.0        NaN   

   export_vpq  
0         NaN  
1         NaN  

[2 rows x 23 columns]

In [790]:
products_tobacco = list(df_tobacco.item_trades.unique())[:-1]
show_production_all_countries(df_tobacco, 2016, products_tobacco, coloring='profit', filename='folium/tobacco_2016_profit.html', cmap='RdYlGn', diverging=True)

In [791]:
df_wheat = pd.read_pickle("./data/wheat_df.pkl")
df_wheat.fillna(0, inplace=True)
df_wheat['profit'] = df_wheat['export_v'] - df_wheat['import_v']
df_wheat['diff_quantity'] = df_wheat['export_q'] - df_wheat['import_q']
df_wheat['import_vpq'] = df_wheat['import_v'] / df_wheat['import_q']
df_wheat['export_vpq'] = df_wheat['export_v'] / df_wheat['export_q']
df_wheat.head(2)

area_code item_crops item_key  year  area_harvested  production  yield  \
0          1      Wheat    wheat  1961             0.0         0.0    0.0   
1          1      Wheat    wheat  1961             0.0         0.0    0.0   

   item_trades  export_q  export_v  ...  ISO3 Code  hs12_code parent_group  \
0  Bran, wheat       0.0       0.0  ...        ARM     100111           10   
1       Bulgur       0.0       0.0  ...        ARM     100111           10   

  child_group parent_description child_description profit diff_quantity  \
0        1001            Cereals  Wheat and meslin    0.0           0.0   
1        1001            Cereals  Wheat and meslin    0.0           0.0   

  import_vpq  export_vpq  
0        NaN         NaN  
1        NaN         NaN  

[2 rows x 23 columns]

In [792]:
products_wheat = list(df_wheat.item_trades.unique())[::-1]
show_production_all_countries(df_wheat, 2016, products_wheat, coloring='profit', filename='folium/wheat_2016_profit.html', cmap='RdYlGn', diverging=True, normalized=False)

In [793]:
show_production_all_countries(df_wheat, 2016, products_wheat, coloring='diff_quantity', filename='folium/wheat_2016_diff_quantity.html', cmap='RdYlGn', diverging=True, normalized=False)

In [806]:
def to_hex_c(color):
    res = hex(int(color * 255))[2:]
    return '0' + res if len(res) == 1 else res

def show_step_production_all_countries(df, year, products=None, coloring='profit', filename='folium/countries_profit.html', cmap='inferno', diverging=False, normalized=True):
    """
    Complete function that takes some predefined df and output a map of the requested food for a given year.
    Show a folium map and then save the plot in an html file
    """
    
    
    df = df[df['year'] == year]
    df = df.replace([np.inf, -np.inf], np.nan)
    world = geopandas.read_file(geopandas.datasets.get_path('naturalearth_lowres'))
    
    # Debugging known anomalies
    world.at[21, 'iso_a3'] = 'NOR'
    world.at[43, 'iso_a3'] = 'FRA'
    world.at[160, 'iso_a3'] = 'CYP'
    world.at[167, 'iso_a3'] = 'SOM'
    world.at[174, 'iso_a3'] = 'RKS'
    
    df = df.merge(world[['pop_est', 'iso_a3']], left_on='ISO3 Code', right_on='iso_a3', how='outer')
    global_min = 0
    global_max = 1
    highest_population = world['pop_est'].max()
    if normalized:
        
        df['profit_norm'] = df['profit'] / df['pop_est']
        df['export_v_norm'] = df['export_v'] / df['pop_est']
        df['import_v_norm'] = df['import_v'] / df['pop_est']
        df['diff_quantity_norm'] = df['diff_quantity'] / df['pop_est']
        df['export_q_norm'] = df['export_q'] / df['pop_est']
        df['import_q_norm'] = df['import_q'] / df['pop_est']
    
    isFirst = True
        
    if products == None:
        products = df.item_trades[:10]
    
    
    #layer_types = ['value', 'quantity']
    m = folium.Map([40,0], zoom_start=2, min_zoom=2)
    #fg = folium.FeatureGroup(overlay=True, name='groups', control=False)
    #m.add_child(fg)
    
    by_product = df.groupby('item_trades')
    for i, product in enumerate(products):
        df_product = by_product.get_group(product)
        
        global_min = min(global_min, df_product[coloring].min())
        global_max = max(global_max, df_product[coloring].max())

        countries = geopandas.read_file('data/world-countries.json')
        #cm = countries.merge(df, left_on='id', right_on='iso3_code')
        cm = countries.merge(df_product, left_on='id', right_on='ISO3 Code')
        
        if i%2 == 0:
            cm.sort_values(by='export_q', ascending=False, inplace=True)
        else:
            cm.sort_values(by='import_q', ascending=False, inplace=True)
        cm = cm[:20]
             
        
        cm['profit'] = cm['profit'].apply(lambda value : 0 if math.isnan(value) else f'{int(value):,}')
        cm['export_v'] = cm['export_v'].apply(lambda value : 0 if math.isnan(value) else f'{int(value):,}')
        cm['import_v'] = cm['import_v'].apply(lambda value : 0 if math.isnan(value) else f'{int(value):,}')
        cm['pop_est'] = cm['pop_est'].apply(lambda value : 0 if math.isnan(value) else f'{int(value):,}')

        cm['diff_quantity'] = cm['diff_quantity'].apply(lambda value : 0 if math.isnan(value) else f'{int(value):,}')
        cm['export_q'] = cm['export_q'].apply(lambda value : 0 if math.isnan(value) else f'{int(value):,}')
        cm['import_q'] = cm['import_q'].apply(lambda value : 0 if math.isnan(value) else f'{int(value):,}')

        cm['export_vpq'] = cm['export_vpq'].apply(lambda value : 0 if math.isnan(value) else f'{value:.2f}')
        cm['import_vpq'] = cm['import_vpq'].apply(lambda value : 0 if math.isnan(value) else f'{value:.2f}')
        cm['index'] = i
        cm['product'] = product
        
        if normalized:
            cm = cm[['id', 'name', 'pop_est', 'product', 'profit_norm', 'export_v_norm', 'import_v_norm', 'diff_quantity_norm', 'export_q_norm', 'import_q_norm',
                 'geometry', 'item_trades', 'export_q', 'import_q', 'export_v', 'import_v', 'ISO3 Code', 'profit', 'diff_quantity', 'import_vpq', 'export_vpq', 'index']]
        else:
            cm = cm[['id', 'name', 'pop_est', 'product',
                 'geometry', 'item_trades', 'export_q', 'import_q', 'export_v', 'import_v', 'ISO3 Code', 'profit', 'diff_quantity', 'import_vpq', 'export_vpq', 'index']]

                
        cm.to_file("data/countries-production.json", driver='GeoJSON')
        geo_json_data = json.load(open('data/countries-production.json'))
        
        def choose_color_function(feature):
            return ([my_color_function1, my_color_function2, my_color_function3, my_color_function4])[feature['properties']['index']]

        def my_color_function1(feature):
            """Maps high values to green and negative values to red."""
            
            color_feature = "export_q"
            if normalized:
                color_feature += "_norm"
            
            
            if len(df[df['ISO3 Code'] == feature['properties']['id']][color_feature]) == 0:
                return '#ffffff'
            value = df[(df['ISO3 Code'] == feature['properties']['id'])&(df['item_trades'] == feature['properties']['item_trades'])][color_feature].iloc[0]
            feat = feature['properties']['item_trades']
            min_val = (df[df['item_trades']== feat])[color_feature].min()
            max_val = (df[df['item_trades']== feat])[color_feature].max()
            min_val = 0 if math.isinf(min_val) else min_val
            max_val = 100000 if math.isinf(max_val) else max_val

            if math.isnan(value) or math.isinf(value):
                return "#BEBEBE"
            
            
            
            colormap = plt.get_cmap('Blues')
            if diverging:
                if value > 0:
                    color = colormap(0.5 + value/(2*max_val))
                else:
                    color = colormap(0.5 - value/(2*min_val))
            else:
                color = colormap( (value - min_val)/(max_val - min_val))
                
                
            return '#' + to_hex_c(color[0]) + to_hex_c(color[1]) + to_hex_c(color[2])
        
        def my_color_function2(feature):
            """Maps high values to green and negative values to red."""
            
            color_feature = "import_q"
            if normalized:
                color_feature += "_norm"
            
            
            if len(df[df['ISO3 Code'] == feature['properties']['id']][color_feature]) == 0:
                return '#ffffff'
            value = df[(df['ISO3 Code'] == feature['properties']['id'])&(df['item_trades'] == feature['properties']['item_trades'])][color_feature].iloc[0]
            feat = feature['properties']['item_trades']
            min_val = (df[df['item_trades']== feat])[color_feature].min()
            max_val = (df[df['item_trades']== feat])[color_feature].max()
            min_val = 0 if math.isinf(min_val) else min_val
            max_val = 100000 if math.isinf(max_val) else max_val

            if math.isnan(value) or math.isinf(value):
                return "#BEBEBE"
            
            
            
            colormap = plt.get_cmap('Purples')
            if diverging:
                if value > 0:
                    color = colormap(0.5 + value/(2*max_val))
                else:
                    color = colormap(0.5 - value/(2*min_val))
            else:
                color = colormap( (value - min_val)/(max_val - min_val))
                
                
            return '#' + to_hex_c(color[0]) + to_hex_c(color[1]) + to_hex_c(color[2])
        
        def my_color_function3(feature):
            """Maps high values to green and negative values to red."""
            
            color_feature = 'export_q'
            if normalized:
                color_feature += "_norm"
            
            
            if len(df[df['ISO3 Code'] == feature['properties']['id']][color_feature]) == 0:
                return '#ffffff'
            value = df[(df['ISO3 Code'] == feature['properties']['id'])&(df['item_trades'] == feature['properties']['item_trades'])][color_feature].iloc[0]
            feat = feature['properties']['item_trades']
            min_val = (df[df['item_trades']== feat])[color_feature].min()
            max_val = (df[df['item_trades']== feat])[color_feature].max()
            min_val = 0 if math.isinf(min_val) else min_val
            max_val = 100000 if math.isinf(max_val) else max_val

            if math.isnan(value) or math.isinf(value):
                return "#BEBEBE"
            
            
            
            colormap = plt.get_cmap('Oranges')
            if diverging:
                if value > 0:
                    color = colormap(0.5 + value/(2*max_val))
                else:
                    color = colormap(0.5 - value/(2*min_val))
            else:
                color = colormap( (value - min_val)/(max_val - min_val))
                
                
            return '#' + to_hex_c(color[0]) + to_hex_c(color[1]) + to_hex_c(color[2])
        def my_color_function4(feature):
            """Maps high values to green and negative values to red."""
            
            color_feature = 'import_q'
            if normalized:
                color_feature += "_norm"
            
            
            if len(df[df['ISO3 Code'] == feature['properties']['id']][color_feature]) == 0:
                return '#ffffff'
            value = df[(df['ISO3 Code'] == feature['properties']['id'])&(df['item_trades'] == feature['properties']['item_trades'])][color_feature].iloc[0]
            feat = feature['properties']['item_trades']
            min_val = (df[df['item_trades']== feat])[color_feature].min()
            max_val = (df[df['item_trades']== feat])[color_feature].max()
            min_val = 0 if math.isinf(min_val) else min_val
            max_val = 100000 if math.isinf(max_val) else max_val

            if math.isnan(value) or math.isinf(value):
                return "#BEBEBE"
            
            
            
            colormap = plt.get_cmap('Reds')
            if diverging:
                if value > 0:
                    color = colormap(0.5 + value/(2*max_val))
                else:
                    color = colormap(0.5 - value/(2*min_val))
            else:
                color = colormap( (value - min_val)/(max_val - min_val))
                
                
            return '#' + to_hex_c(color[0]) + to_hex_c(color[1]) + to_hex_c(color[2])
            
            
            

        def my_highlight_function(feature):
            return {
                'fillColor': 'black',
                'fillOpacity': 0.5,
                'color' : 'black',
                'weight' : 3,
                'dashArray' : '5, 5'
                }

        
        layer = folium.GeoJson(
            geo_json_data,
            style_function=lambda feature: {
                'fillColor': choose_color_function(feature)(feature),
                'fillOpacity': 0.5,
                'color' : 'black',
                'weight' : 1.5,
                'dashArray' : '5, 5'
                },
            overlay=True,
            show=isFirst,
            highlight_function=my_highlight_function,
            tooltip=folium.features.GeoJsonTooltip(
                opacity=1,
                fields=['name', 'pop_est', 'product', 'profit', 'export_v', 'import_v', 'diff_quantity', 'export_q', 'import_q', 'export_vpq', 'import_vpq'],
                aliases=['State name:', 'population estimation [Hab.]:', 'product:',  'Gross Profit [1,000$]:', 'Export value [1,000$]:', 'Import value [1,000$]: ', 'Difference of quantity [Tonnes]:', 'Export quantity [Tonnes]:', 'Import quantity [Tonnes]:', 'Export V/Q [1,000$/Tonnes]:', 'Import V/Q [1,000$/Tonnes]:'],
                )
            )
        #g = plugins.FeatureGroupSubGroup(fg, coloring, show=False)
        #m.add_child(g)
        isFirst = True
        
        map_color = ['Blue', 'Purple', 'Orange', 'Red']
        
        layer.layer_name = product + ' Export (in ' + map_color[i] + ')' if i % 2 == 0 else product + ' Import (in ' + map_color[i] + ')'
        layer.add_to(m)
        
        
        #layer.add_to(fg)
        
    plugins.Fullscreen(
        position='bottomright',
        title='Expand me',
        title_cancel='Exit me',
        force_separate_button=True
    ).add_to(m)
    if normalized:
        global_min /= highest_population
        global_max /= highest_population
        
    colormapL = branca.colormap.LinearColormap(colors=['blue','purple','orange', 'red'], index=[0,1,2,3],vmin=0,vmax=3)
    
    
    title = {'profit' : 'Gross Profit', 'diff_quantity' : 'Difference of Quantity', 'import_q' : 'import Quantity', 'export_q': 'Export Quantity',
            'import_v': 'Import Value', 'export_v' : 'Export Value', 'import_vpq' : 'Import Value per Quantity', 'export_vpq' : 'Export Value per Quantity'}
    colormapL.caption = "Tobacco Exporters, Tobacco Importers, Cigarette Exporters, Cigarette Importers"
    colormapL.add_to(m)  
    folium.LayerControl().add_to(m)
    
    m.save(filename)
    return m

In [807]:
# top 20 producers (exporters), importers, TABACS - CIGARETTES /// UN_NORMALIZED QUANTITY


In [808]:
products_tobacco = ['Tobacco, unmanufactured', 'Tobacco, unmanufactured', 'Cigarettes', 'Cigarettes']
show_step_production_all_countries(df_tobacco, 2016, products_tobacco, coloring='profit', filename='folium/tobacco_2016_profit.html', cmap='RdYlGn', diverging=True, normalized=False)